In [2]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt

from sklearn.feature_extraction import DictVectorizer
from sklearn.linear_model import LinearRegression 
from sklearn.linear_model import Lasso 
from sklearn.metrics import mean_squared_error

import pickle

/home/codespace/anaconda3/lib/python3.9/site-packages/pandas/core/computation/expressions.py:21: UserWarning: Pandas requires version '2.8.4' or newer of 'numexpr' (version '2.8.1' currently installed).
  from pandas.core.computation.check import NUMEXPR_INSTALLED
/home/codespace/anaconda3/lib/python3.9/site-packages/pandas/core/arrays/masked.py:61: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.4' currently installed).
  from pandas.core import (


In [4]:
import mlflow

mlflow.set_tracking_uri("sqlite:///mlflow.db")
mlflow.set_experiment("taxi-exp")

2026/01/06 16:02:35 INFO mlflow.store.db.utils: Creating initial MLflow database tables...
2026/01/06 16:02:35 INFO mlflow.store.db.utils: Updating database tables
INFO  [alembic.runtime.migration] Context impl SQLiteImpl.
INFO  [alembic.runtime.migration] Will assume non-transactional DDL.
INFO  [alembic.runtime.migration] Context impl SQLiteImpl.
INFO  [alembic.runtime.migration] Will assume non-transactional DDL.
2026/01/06 16:02:35 INFO mlflow.tracking.fluent: Experiment with name 'taxi-exp' does not exist. Creating a new experiment.


<Experiment: artifact_location='/workspaces/mlops-course/02-exp-track/mlruns/1', creation_time=1767715355269, experiment_id='1', last_update_time=1767715355269, lifecycle_stage='active', name='taxi-exp', tags={}>

In [6]:
def read_df(filename):
    df = pd.read_parquet(filename)

    df.lpep_pickup_datetime = pd.to_datetime(df.lpep_pickup_datetime)
    df.lpep_dropoff_datetime = pd.to_datetime(df.lpep_dropoff_datetime)

    df['duration'] = df.lpep_dropoff_datetime - df.lpep_pickup_datetime
    df.duration = df.duration.apply(lambda td : td.total_seconds()/60)

    df = df[(df.duration >= 1) & (df.duration <= 60)]

    categorical = ['PULocationID' , 'DOLocationID']
    df[categorical] = df[categorical].astype(str)
    
    return df
                         

In [7]:
df_train = read_df('./data/green_tripdata_2021-01.parquet')
df_val = read_df('./data/green_tripdata_2021-02.parquet')

In [8]:
df_train['PU_DO'] = df_train['PULocationID'] + '_' + df_train['DOLocationID']
df_val['PU_DO'] = df_val['PULocationID'] + '_' + df_val['DOLocationID']

In [9]:
# categorical = ['PULocationID', 'DOLocationID']
categorical = ['PU_DO']
numerical = ['trip_distance']

dv = DictVectorizer()
train_dicts = df_train[categorical+numerical].to_dict(orient='records')
X_train = dv.fit_transform(train_dicts)

val_dicts = df_val[categorical+numerical].to_dict(orient='records')
X_val = dv.transform(val_dicts)

target = 'duration'
y_train = df_train[target].values

y_val = df_val[target].values

In [9]:
lr = LinearRegression()
lr.fit(X_train, y_train)

y_pred = lr.predict(X_val)

mean_squared_error(y_val, y_pred, squared=False)

7.4795869498500265

In [10]:
with open('models/lin_reg.bin', 'wb') as f_out:
    pickle.dump((dv, lr), f_out)

In [16]:
with mlflow.start_run():
    
    mlflow.set_tag("taxi experiment", "ayush")
    
    mlflow.log_param("train-data-path","./data/green_tripdata_2021-01.parquet")
    mlflow.log_param("val-data-path","./data/green_tripdata_2021-02.parquet")    
    
    alpha = 0.1
    
    mlflow.log_param("alpha",alpha)
    
    lr = Lasso(alpha)
    lr.fit(X_train, y_train)
    
    y_pred = lr.predict(X_val)
    rmse = mean_squared_error(y_val, y_pred, squared=False)
    
    mlflow.log_metric("rmse", rmse)

In [4]:
import xgboost as xgb

from hyperopt import fmin, tpe, hp, STATUS_OK, Trials
from hyperopt.pyll import scope

In [20]:
# fmin - function to find minimum among all
# tpe - algorithm for the optimal values
# hp - to define hyperparameter in search space

In [10]:
train = xgb.DMatrix(X_train, label = y_train)
val = xgb.DMatrix(X_val, label = y_val)

In [29]:
def objective(params):
    
    with mlflow.start_run():
        mlflow.set_tag("taxi-exp-new-model","xgboost")
        mlflow.log_params(params)
        booster = xgb.train(
            params = params,
            dtrain = train,
            num_boost_round = 1000,
            evals = [(val, "validation")],
            early_stopping_rounds = 50
        )
        y_pred = booster.predict(val)
        rmse = mean_squared_error(y_val, y_pred, squared = False)
        mlflow.log_metric("rmse",rmse)
    
    return {'loss':rmse, 'status':STATUS_OK}

In [30]:
search_space = {
    'max_depth' : scope.int(hp.quniform('max_depth', 4, 100, 1)),
    'learning_rate' : hp.loguniform('learning_rate', -3, 0),
    'reg_alpha' : hp.loguniform('reg_alpha', -5, -1),
    'reg_lambda' : hp.loguniform('reg_lambda', -6, -1),
    'min_child_weight' : hp.loguniform('min_child_weight', -1, 3),
    'objective' : 'reg:linear',
    'seed' : 42,
}

best_results = fmin(
    fn = objective,
    space = search_space,
    algo = tpe.suggest,
    max_evals = 50,
    trials = Trials()
)

  0%|                                                                                                                   | 0/50 [00:00<?, ?trial/s, best loss=?]

/home/codespace/anaconda3/lib/python3.9/site-packages/xgboost/core.py:158: UserWarning: [17:18:02] WARNING: /workspace/src/objective/regression_obj.cu:227: reg:linear is now deprecated in favor of reg:squarederror.
  warnings.warn(smsg, UserWarning)



[0]	validation-rmse:11.50091                                                                                                                                   
[1]	validation-rmse:10.87272                                                                                                                                   
[2]	validation-rmse:10.32046                                                                                                                                   
[3]	validation-rmse:9.83662                                                                                                                                    
[4]	validation-rmse:9.41413                                                                                                                                    
[5]	validation-rmse:9.04641                                                                                                                                    
[6]	validation-rmse:8.72694             

[51]	validation-rmse:6.70181                                                                                                                                   
[52]	validation-rmse:6.70013                                                                                                                                   
[53]	validation-rmse:6.69847                                                                                                                                   
[54]	validation-rmse:6.69702                                                                                                                                   
[55]	validation-rmse:6.69559                                                                                                                                   
[56]	validation-rmse:6.69474                                                                                                                                   
[57]	validation-rmse:6.69353            

[102]	validation-rmse:6.67911                                                                                                                                  
[103]	validation-rmse:6.67889                                                                                                                                  
[104]	validation-rmse:6.67863                                                                                                                                  
[105]	validation-rmse:6.67853                                                                                                                                  
[106]	validation-rmse:6.67850                                                                                                                                  
[107]	validation-rmse:6.67824                                                                                                                                  
[108]	validation-rmse:6.67817           

...

[768]	validation-rmse:6.54947                                                                                                                                  
[769]	validation-rmse:6.54929                                                                                                                                  
[770]	validation-rmse:6.54916                                                                                                                                  
[771]	validation-rmse:6.54909                                                                                                                                  
[772]	validation-rmse:6.54893                                                                                                                                  
[773]	validation-rmse:6.54875                                                                                                                                  
[774]	validation-rmse:6.54866           

[819]	validation-rmse:6.54364                                                                                                                                  
[820]	validation-rmse:6.54355                                                                                                                                  
[821]	validation-rmse:6.54323                                                                                                                                  
[822]	validation-rmse:6.54303                                                                                                                                  
[823]	validation-rmse:6.54281                                                                                                                                  
[824]	validation-rmse:6.54275                                                                                                                                  
[825]	validation-rmse:6.54254           

[870]	validation-rmse:6.53718                                                                                                                                  
[871]	validation-rmse:6.53707                                                                                                                                  
[872]	validation-rmse:6.53692                                                                                                                                  
[873]	validation-rmse:6.53688                                                                                                                                  
[874]	validation-rmse:6.53667                                                                                                                                  
[875]	validation-rmse:6.53651                                                                                                                                  
[876]	validation-rmse:6.53652           

[921]	validation-rmse:6.53257                                                                                                                                  
[922]	validation-rmse:6.53251                                                                                                                                  
[923]	validation-rmse:6.53221                                                                                                                                  
[924]	validation-rmse:6.53222                                                                                                                                  
[925]	validation-rmse:6.53212                                                                                                                                  
[926]	validation-rmse:6.53207                                                                                                                                  
[927]	validation-rmse:6.53201           

[972]	validation-rmse:6.52811                                                                                                                                  
[973]	validation-rmse:6.52804                                                                                                                                  
[974]	validation-rmse:6.52797                                                                                                                                  
[975]	validation-rmse:6.52794                                                                                                                                  
[976]	validation-rmse:6.52787                                                                                                                                  
[977]	validation-rmse:6.52786                                                                                                                                  
[978]	validation-rmse:6.52779           

In [13]:
params = {
    'learning_rate': 0.37757498979853754,
    'max_depth' : 12,
    'min_child_weight' : 1.8053027317262507,
    'objective' : 'reg:linear',
    'reg_alpha' : 0.0690841157723101,
    'reg_lambda' : 0.0160545759256956 , 
    'seed' : 42
}

mlflow.xgboost.autolog()

booster = xgb.train(
    params = params,
    dtrain = train,
    num_boost_round = 1000,
    evals = [(val, "validation")],
    early_stopping_rounds = 50
)

2026/01/06 19:10:31 WARNING mlflow.utils.autologging_utils: MLflow autologging encountered a warning: "/home/codespace/anaconda3/lib/python3.9/site-packages/xgboost/core.py:158: UserWarning: [19:10:31] WARNING: /workspace/src/objective/regression_obj.cu:227: reg:linear is now deprecated in favor of reg:squarederror."


[0]	validation-rmse:9.40390
[1]	validation-rmse:7.98488
[2]	validation-rmse:7.30913
[3]	validation-rmse:6.98872
[4]	validation-rmse:6.83623
[5]	validation-rmse:6.75771
[6]	validation-rmse:6.71778
[7]	validation-rmse:6.68874
[8]	validation-rmse:6.67463
[9]	validation-rmse:6.66214
[10]	validation-rmse:6.65581
[11]	validation-rmse:6.65350
[12]	validation-rmse:6.64979
[13]	validation-rmse:6.64551
[14]	validation-rmse:6.64119
[15]	validation-rmse:6.63695
[16]	validation-rmse:6.63338
[17]	validation-rmse:6.62937
[18]	validation-rmse:6.62677
[19]	validation-rmse:6.62516
[20]	validation-rmse:6.62166
[21]	validation-rmse:6.61899
[22]	validation-rmse:6.61772
[23]	validation-rmse:6.61642
[24]	validation-rmse:6.61385
[25]	validation-rmse:6.61171
[26]	validation-rmse:6.60788
[27]	validation-rmse:6.60602
[28]	validation-rmse:6.60380
[29]	validation-rmse:6.60110
[30]	validation-rmse:6.59911
[31]	validation-rmse:6.59829
[32]	validation-rmse:6.59554
[33]	validation-rmse:6.59431
[34]	validation-rmse:6.5

[277]	validation-rmse:6.39468
[278]	validation-rmse:6.39491
[279]	validation-rmse:6.39455
[280]	validation-rmse:6.39384
[281]	validation-rmse:6.39363
[282]	validation-rmse:6.39235
[283]	validation-rmse:6.39190
[284]	validation-rmse:6.39102
[285]	validation-rmse:6.39060
[286]	validation-rmse:6.39012
[287]	validation-rmse:6.38979
[288]	validation-rmse:6.38920
[289]	validation-rmse:6.38917
[290]	validation-rmse:6.38863
[291]	validation-rmse:6.38830
[292]	validation-rmse:6.38832
[293]	validation-rmse:6.38849
[294]	validation-rmse:6.38791
[295]	validation-rmse:6.38831
[296]	validation-rmse:6.38800
[297]	validation-rmse:6.38803
[298]	validation-rmse:6.38736
[299]	validation-rmse:6.38672
[300]	validation-rmse:6.38675
[301]	validation-rmse:6.38634
[302]	validation-rmse:6.38632
[303]	validation-rmse:6.38575
[304]	validation-rmse:6.38562
[305]	validation-rmse:6.38524
[306]	validation-rmse:6.38527
[307]	validation-rmse:6.38496
[308]	validation-rmse:6.38501
[309]	validation-rmse:6.38475
[310]	vali

[551]	validation-rmse:6.33770
[552]	validation-rmse:6.33767
[553]	validation-rmse:6.33794
[554]	validation-rmse:6.33787
[555]	validation-rmse:6.33775
[556]	validation-rmse:6.33712
[557]	validation-rmse:6.33675
[558]	validation-rmse:6.33642
[559]	validation-rmse:6.33650
[560]	validation-rmse:6.33632
[561]	validation-rmse:6.33601
[562]	validation-rmse:6.33613
[563]	validation-rmse:6.33608
[564]	validation-rmse:6.33612
[565]	validation-rmse:6.33598
[566]	validation-rmse:6.33595
[567]	validation-rmse:6.33556
[568]	validation-rmse:6.33572
[569]	validation-rmse:6.33590
[570]	validation-rmse:6.33582
[571]	validation-rmse:6.33585
[572]	validation-rmse:6.33549
[573]	validation-rmse:6.33542
[574]	validation-rmse:6.33531
[575]	validation-rmse:6.33527
[576]	validation-rmse:6.33550
[577]	validation-rmse:6.33549
[578]	validation-rmse:6.33528
[579]	validation-rmse:6.33483
[580]	validation-rmse:6.33473
[581]	validation-rmse:6.33455
[582]	validation-rmse:6.33457
[583]	validation-rmse:6.33207
[584]	vali

[825]	validation-rmse:6.31589
[826]	validation-rmse:6.31560
[827]	validation-rmse:6.31552
[828]	validation-rmse:6.31542
[829]	validation-rmse:6.31527
[830]	validation-rmse:6.31514
[831]	validation-rmse:6.31494
[832]	validation-rmse:6.31477
[833]	validation-rmse:6.31483
[834]	validation-rmse:6.31459
[835]	validation-rmse:6.31478
[836]	validation-rmse:6.31479
[837]	validation-rmse:6.31515
[838]	validation-rmse:6.31501
[839]	validation-rmse:6.31501
[840]	validation-rmse:6.31510
[841]	validation-rmse:6.31506
[842]	validation-rmse:6.31529
[843]	validation-rmse:6.31557
[844]	validation-rmse:6.31570
[845]	validation-rmse:6.31577
[846]	validation-rmse:6.31579
[847]	validation-rmse:6.31564
[848]	validation-rmse:6.31591
[849]	validation-rmse:6.31593
[850]	validation-rmse:6.31600
[851]	validation-rmse:6.31593
[852]	validation-rmse:6.31604
[853]	validation-rmse:6.31613
[854]	validation-rmse:6.31486
[855]	validation-rmse:6.31432
[856]	validation-rmse:6.31393
[857]	validation-rmse:6.31381
[858]	vali

2026/01/06 19:11:50 WARNING mlflow.utils.autologging_utils: Encountered unexpected error during xgboost autologging: Could not find experiment with ID 0
